In [ ]:
!pip install openai

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import json
import pandas as pd
import os
import re
from openai import OpenAI
import json
import pandas as pd
from math import ceil




In [ ]:
data_path = '/content/drive/MyDrive/Grad/CSC2615/Project/aita_800_new_posts.json'

with open(data_path, 'r') as f:
    dataset = json.load(f)

print("JSON data loaded successfully.")


JSON data loaded successfully.


In [ ]:
# numer of posts in dataset
print("Number of posts in dataset: ", len(dataset))
# taking a look at the data
print('Sample data in list: ', dataset[0])

# data keys
print('One post dictionary keys: ', dataset[0].keys())

Number of posts in dataset:  800
Sample data in list:  {'post_id': 'zb004v', 'title': 'AITA for calling my mother-in-law multiple times to check up on my baby while I was on a trip with my husband?', 'post': 'I went on a 3-day trip with my husband. I didn’t want to go as our baby is only 8 months and being away from him for more than a few hours and a plane ride away made me feel anxious but going on the trip was important to my husband so I agreed to go.\n\nI called my mother-in-law multiple times to check up on my son while I was away. She told me he was fine every time but I kept calling whenever I was worried. My husband asked me to stop as he said I was ruining the trip and I would make his parents feel like I didn’t trust them with our son. During the trip we had dinner with an associate of my husband’s and I excused myself twice so I could call to see if my son was okay as the first time he was crying.\n\nWhen we got back to the hotel my husband was really angry at me and he sai

In [ ]:
print(len(dataset[0]['top_level_comments']), 'comments in first story')
print('Sample data in top_level_comments: ',dataset[0]['top_level_comments'])
print('top_level_comments keys: ', dataset[0]['top_level_comments'][0].keys())

100 comments in first story
Sample data in top_level_comments:  [{'comment_id': 'iyoggdu', 'text': "This isn't an AITA problem, this is a marriage counseling problem", 'score': 61, 'created_utc': 1670020291, 'label': None}, {'comment_id': 'iyogn4q', 'text': 'Asshole and marriage problem', 'score': -4, 'created_utc': 1670020378, 'label': None}, {'comment_id': 'iyogov8', 'text': 'How many times a day did you call? Like 3-6 seems valid.  20 is too much', 'score': 114, 'created_utc': 1670020400, 'label': None}, {'comment_id': 'iyogrg0', 'text': 'YTA \n\nCalling to check isn’t the problem, it was obsessively calling that was. You called twice during a dinner, I am unsurprised that your husband was unhappy.', 'score': 3135, 'created_utc': 1670020432, 'label': 'YTA'}, {'comment_id': 'iyogshz', 'text': "I'd say NTA from the perspective of hearing about separation anxiety when it comes to a mother being away from her baby.Tho, I think you should try to discuss with you husband again, and deffo 

In [ ]:
print('Total number of comments in all posts:', sum([len(post['top_level_comments']) for post in dataset]))

Total number of comments in all posts: 76604


In [ ]:
import json

def batch_iterable(items, batch_size):
    """Yields batches from an iterable."""
    for i in range(0, len(items), batch_size):
        yield items[i : i + batch_size]

def generate_comments_by_post(post: dict, batch_size_limit: int = 20):
    """
    Generates processed comments for a post, batching inputs to LLM safely.
    Ensures GPT output is always parsed as a single JSON array.
    """

    print(f"Processing Post: {post['post_id']}, Number of comments in this post: {len(post['top_level_comments'])}")

    post_dict = {
        "post_id": post["post_id"],
        "title": post["title"],
        "post": post["post"],
        "processed_comments": []
    }

    if not post['top_level_comments']:
        return post_dict  # No comments, return early

    for batch in batch_iterable(post['top_level_comments'], batch_size_limit):

        items_block = [
            {
                "comment_id": row["comment_id"],
                "comment": row["text"],
                "comment_label": row["label"],
                "comment_score": row["score"]
            }
            for row in batch
        ]

        system_prompt = """You are a fair and neutral comment evaluator. Your task is to evaluate comments on a Reddit "Am I the Asshole" (AITA) post.

You will:
1. Analyze what the comment believes about the original poster (OP) in terms of intentionality, harm, empathy, and apology.
2. Evaluate the quality of the comment itself along several dimensions of argumentative and moral quality based on well established moral frameworks.

You will be provided with:
- The title of the post.
- The content of the post.
- The comment.
- The label of the comment:
    - YTA ("You're the A**hole") – The OP is judged to be primarily or entirely in the wrong.
    - NTA ("Not the A**hole") – The OP's actions are deemed justified or appropriate.
    - NAH ("No A**holes Here") – A conflict occurred but no-one is clearly the "a**hole".
    - ESH ("Everybody Sucks Here") – All parties are considered to have acted poorly.
- The comment popularity (upvotes - downvotes).

Return a JSON object with a single key 'analyses', which is an array where each element has keys:
- comment_id (string)
- comment_content_vector (list of 4 integers 0 or 1): features [harm, intentionality, empathy, apology].
- comment_quality_vector (list of 5 integers 1–5): features [justification_strength, ethical_principle_articulation, deliberative_quality, fairness_of_blame, nonbiased_language].
- reasoning (string): a very short explanation of your vector values. This should be at most two short sentences.

DEFINITIONS

- Comment Content Vector:
  This reflects what the COMMENT believes about the OP, not your own opinion.  
  Each dimension is grounded in explicit moral theories to maintain interpretive consistency.

  - intentionality:  
    This follows Gray and Wegner’s Dyadic Morality framework (Schein & Gray, 2018), where intent is a key component of assigning moral agency.  
    true if the comment implies OP acted deliberately or knowingly; false if it treats the action as accidental, unintentional, or unclear.

  - harm:  
    Also grounded in Dyadic Morality (Schein & Gray, 2018), which requires a perceived “Patient” who experiences suffering.  
    true if the comment implies OP caused meaningful emotional, physical, social, or financial harm; false if it denies harm or frames the impact as negligible.

  - empathy:  
    Based on the Care/Harm foundation within Haidt’s Moral Foundations Theory (Graham, Haidt, & Nosek, 2013).  
    true if the comment portrays OP as considerate of others’ feelings; false if the comment frames OP as indifferent, callous, or lacking care.

  - apology:  
    Grounded in Benoit’s Image Repair Theory (Benoit, 1997), which identifies apology and corrective effort as key mechanisms for reframing wrongdoing.  
    true if the comment implies OP has apologized, attempted repair, or clearly should apologize; false if apology or repair is absent, unnecessary, or dismissed.

- Comment Quality Vector (1 = very poor, 5 = excellent):
  These dimensions evaluate the epistemic and moral reliability of the comment using established frameworks in argumentation and moral philosophy.

  justification_strength:
    Based on Toulmin’s Argumentation Model (Toulmin, 1958), which requires claims to be supported by explicit warrants and evidence.  
    How clearly and specifically the comment justifies its verdict using details from the post.

  ethical_principle_articulation:
    Draws on Moral Foundations Theory (Graham, Haidt, & Nosek, 2013) as a schema for identifying invoked moral values (fairness, harm, consent, autonomy, respect).  
    How clearly the comment names and applies moral norms or principles.

  deliberative_quality:
    Also based on Toulmin (1958) regarding reason-giving and constructive discourse.  
    Respectful tone, engagement with OP/others, and constructiveness (e.g., advice or alternatives rather than pure attack).

  fairness_of_blame:
    Grounded in Adam Smith’s Ideal Observer Theory (Smith, 1759), which emphasizes impartiality and proportional judgment.  
    Whether the comment considers multiple perspectives, applies consistent standards, and assigns blame proportionately.

  nonbiased_language:
    Also rooted in Ideal Observer Theory (Smith, 1759), requiring judgments free from prejudice or identity-based distortion.  
    Whether the comment avoids stereotypes, slurs, or double standards.  
    1 = heavily biased language; 5 = explicitly fair, focused on behavior, and may call out bias.


Your output MUST be valid JSON and MUST NOT contain trailing commas or text."""

        user_prompt_string = f"""
Analyze the following Reddit post and its corresponding comments. Your output must strictly follow the required JSON schema for the 'analyses' array.

### POST TITLE ###
{post["title"]}

### POST BODY ###
{post["post"]}

### COMMENTS TO ANALYZE ###
{json.dumps(items_block, indent=2)}
"""

        try:
            response = client.chat.completions.create(
                model="gpt-5.1",
                messages=[
                    {"role": "system", "content": system_prompt},
                    {"role": "user", "content": user_prompt_string}
                ],
                max_completion_tokens=4096,
                temperature=0.2,  # Low for consistency
                response_format={
                    "type": "json_schema",
                    "json_schema": {
                        "name": "comment_analyses",  # Added required name
                        "schema": {
                            "type": "object",
                            "properties": {
                                "analyses": {
                                    "type": "array",
                                    "description": "A list of structured analyses for each comment provided in the user prompt.",
                                    "items": {
                                        "type": "object",
                                        "properties": {
                                            "comment_id": {"type": "string"},
                                            "comment_content_vector": {
                                                "type": "array",
                                                "items": {"type": "integer"},
                                                "minItems": 4,
                                                "maxItems": 4
                                            },
                                            "comment_quality_vector": {
                                                "type": "array",
                                                "items": {"type": "integer"},
                                                "minItems": 5,
                                                "maxItems": 5
                                            },
                                            "reasoning": {"type": "string"}
                                        },
                                        "required": [
                                            "comment_id",
                                            "comment_content_vector",
                                            "comment_quality_vector",
                                            "reasoning"
                                        ]
                                    }
                                }
                            },
                            "required": ["analyses"]
                        }
                    }
                }
            )

            raw_output = json.loads(response.choices[0].message.content)
            final_results_list = raw_output['analyses']
            post_dict["processed_comments"].extend(final_results_list)  # Append the batch results

        except Exception as e:
            print(f"API Error for batch in post {post['post_id']}: {e}")
            # Optional: Add retry logic here if desired

    # Optional: Sort processed_comments by comment_id for consistency
    post_dict["processed_comments"].sort(key=lambda x: x["comment_id"])

    return post_dict


In [ ]:
def load_processed_data(file_path: str):
    """Reads all JSON objects from a JSONL file into a list of dictionaries."""
    if not os.path.exists(file_path):
        return []

    data = []
    with open(file_path, 'r', encoding='utf-8') as f:
        for line in f:
            line = line.strip()
            if line:
                try:
                    data.append(json.loads(line))
                except json.JSONDecodeError as e:
                    print(f"Error parsing line: {line[:50]}... Error: {e}")
    return data


In [ ]:
import json

from openai import OpenAI
from openai import APIError

OPENAI_API_KEY = ''
client = OpenAI(api_key=OPENAI_API_KEY)


In [ ]:

output_filepath = "/content/drive/MyDrive/Grad/CSC2615/Project/processed_comments_800_new_posts.json"
successful_posts = []

In [ ]:
loaded_data = load_processed_data(output_filepath)
print(f"Number of posts in the output file: {len(loaded_data)}")

Number of posts in the output file: 401


In [ ]:
already_proccessed_posts = []
for d in loaded_data:
  already_proccessed_posts.append(d['post_id'])

In [ ]:
print(len(already_proccessed_posts))

397


In [ ]:
i = 0
for post in dataset:
    if post['post_id'] in already_proccessed_posts:
        continue
    if post['post_id'] == 'zqr3gy':
        continue
    if i ==3:
      break
    try:
        post_results = generate_comments_by_post(post)

        with open(output_filepath, "a", encoding="utf-8") as f:
            f.write(json.dumps(post_results) + "\n")

        successful_posts.append(post["post_id"])

    except Exception as e:
        print(f"Error processing Post ID {post['post_id']}: {e}")

In [ ]:
results_loaded = load_processed_data(output_filepath)
display(results_loaded)

[{'post_id': 'ymk63b',
  'title': 'AITA for having a strict “no last minute flaking” policy for when it comes to first dates?',
  'post': 'I see this woman pretty often as she works at a restaurant I go to on my lunch breaks. We make small talk but obviously keep it somewhat professional. This has been going on for months so we are pretty familiar with one another but not necessarily “friends”. I did get the feeling she may be interested in me but she is friendly with everyone so it’s hard to tell. \n\nThe other day we were talking and she gave me her number to finish the conversation since we got interrupted by another customer. I texted saying hi and she said we should grab drinks Thursday night. I agreed and then Thursday came along with no communication the whole day. \n\nAn hour before we agreed to meet I asked her if she needed to be picked up and that’s when she said “Sorry for not texting earlier, I last minute got scheduled for the night shift since the other worker called in 